# xarray-einstats for ArviZ

In [1]:
# needs dask_einops branch of xarray-einstats
import arviz as az
import numpy as np

from utils import rhat_einstats

xarray-einstats versions of rhat. They work on DataArrays (and can be applied to Datasets with `.map`) of _any_ number of dimensions as long as there is a `chain` and a `draw` dimension (like in ArviZ, their actual order doesn't matter though).

## Compare to current performance

In [2]:
post = az.load_arviz_data("centered_eight").posterior
%timeit rhat_einstats(post)
%timeit az.rhat(post)

34.9 ms ± 915 µs per loop (mean ± std. dev. of 7 runs, 10 loops each)
13.2 ms ± 300 µs per loop (mean ± std. dev. of 7 runs, 1 loop each)


For very small Datasets/DataArrays, it is slower than the current implementation. I think this is because
the main overhead when operating with xarray objects is the use of `apply_ufunc` which aligns and dispatches
the array operation on the xarray one, taking dims and coords into account.

In our current implementation, everything is implemented as array functions that work on 2d input only.
We then use `_make_ufunc` to loop over all 2d `chain, draw` chunks and apply that function. `apply_ufunc` is
called only once on that loop based ufunc.

This alternative uses xarray and xarray-einstats directly, so there are now many function calls happening
via `apply_ufunc`.

Both times are perfectly fast, and I don't think performance at this scale should be a concern. When the actual computation starts to be noticeable, this overhead effect is negligible and the xarray-einstats approach
scales much better. It is already faster on datasets of sizes similar to the radon dataset:

In [3]:
post = az.load_arviz_data("radon").posterior
%timeit rhat_einstats(post)
%timeit az.rhat(post)

272 ms ± 2.42 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)
324 ms ± 4.76 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)


## Dask integration and further scaling properties

### Out of memory computation
`az.rhat` is one of the functions that already supports dask in ArviZ, so this would not make something
new possible with arviz, but I think that this approach of computation more integrated with xarray can
be applied to other functions and will be easier for dask integration with all stats and diagnostics.

The first step is showing that both `rhat_einstats` defined here and `az.rhat` can compute rhat on a ~15Gb dataset
from my 8Gb RAM laptop. I have used ~100MB chunks to allow Dask to store multiple chunks in memory while I use the computer and use the browser. Python only has 3-4Gb available to use. It would probably be a bit faster to use slightly larger chunks but that should affect all methods in a similar way.

In [4]:
import dask
import time

data = dask.array.random.normal(size=(4, 1000, 600_000), chunks={2: 3000})
post_dask = az.from_dict({"mu": data}, dims={"mu": ["obs_id"]}).posterior
data

dask.array<normal, shape=(4, 1000, 600000), dtype=float64, chunksize=(4, 1000, 3000), chunktype=numpy.ndarray>

In [5]:
s = time.time()
aux = rhat_einstats(post_dask, method="identity", dask="allowed").compute()
print(time.time() - s)
aux

36.96788024902344


<xarray.Dataset>
Dimensions:  (obs_id: 600000)
Coordinates:
  * obs_id   (obs_id) int64 0 1 2 3 4 5 ... 599995 599996 599997 599998 599999
Data variables:
    mu       (obs_id) float64 0.9997 0.9999 1.0 0.9996 ... 0.9997 0.9996 0.9997

In [6]:
az.Dask.enable_dask(dask_kwargs={"dask": "parallelized"})
s = time.time()
aux = az.rhat(post_dask, method="identity").compute()
print(time.time() - s)
aux

arviz - WARNING - Shape validation failed: input_shape: (1, 1), minimum_shape: (chains=2, draws=4)


105.53762722015381


<xarray.Dataset>
Dimensions:  (obs_id: 600000)
Coordinates:
  * obs_id   (obs_id) int64 0 1 2 3 4 5 ... 599995 599996 599997 599998 599999
Data variables:
    mu       (obs_id) float64 0.9997 0.9999 1.0 0.9996 ... 0.9997 0.9996 0.9997

We see that both work and give the same exact result. The current dask="parallelized" version is significantly slower, even with numba optimizations and even if the scipy part of the xarray-einstats implementation is also using dask="parallelized". Using dask="allowed" whenever possible allows dask to optimize much more the computation graph.

### Parallelized and optimized computation
Note: my idea was to run the comparisons below (except the first case) on `post_dask`, but it took very long and I
wasn't patient enough. So we compare with this dataset below with 6 chunks only. Doing that also has the side advantage of comparing numpy/in memory computation to dask parallelization and show it can even be useful on
data that fits in memory if the computations are expensive.

This section therefore shows again the `rhat_einstats` implementation but it is mostly an overview on the multiple
optimizations available in ArviZ right now side by side with this proposed change.

In [7]:
ds = post_dask.sel(obs_id=np.arange(18_000))
ds.mu.data

dask.array<getitem, shape=(4, 1000, 18000), dtype=float64, chunksize=(4, 1000, 3000), chunktype=numpy.ndarray>

#### `rhat_einstats`
##### In memory computation

In [8]:
s = time.time()
aux = rhat_einstats(ds.compute(), method="rank")
print(time.time() - s)

29.66400647163391


(note that above we computed rhat on 200 chunks instead of 6 chunks in 37 seconds, this should be an indicator on how good Dask is at parallelizing and optimizing the computational graph)

##### Distributed computing

In [9]:
s = time.time()
aux = rhat_einstats(ds, method="rank", dask="allowed").compute()
print(time.time() - s)

20.49239754676819


#### `az.rhat`
##### Dask + Numba

In [10]:
az.Dask.enable_dask(dask_kwargs={"dask": "parallelized"})
az.Numba.enable_numba()
s = time.time()
aux = az.rhat(ds, method="rank").compute()
print(time.time() - s)

58.58326029777527


##### Dask only

In [11]:
az.Dask.enable_dask(dask_kwargs={"dask": "parallelized"})
az.Numba.disable_numba()
s = time.time()
aux = az.rhat(ds, method="rank").compute()
print(time.time() - s)

66.21241903305054


##### Numba only (in memory computation)

In [12]:
az.Dask.disable_dask()
az.Numba.enable_numba()
s = time.time()
aux = az.rhat(ds.compute(), method="rank")
print(time.time() - s)

32.96099853515625


##### No optimizations (in memory computation)

In [13]:
az.Dask.disable_dask()
az.Numba.disable_numba()
s = time.time()
aux = az.rhat(ds.compute(), method="rank")
print(time.time() - s)

34.55539298057556


### Summary

There might be room for some further optimizations in `rhat_einstats` using Numba maybe, but even without them,
it outperforms the current implementation in all relevant cases.

Moreover, in my opinion, the code is simpler and easier to understand. It doesn't need `_make_ufunc` nor `wrap_xarray_ufunc` wrappers, it doesn't have `if numba` statements (that also need duplicated testing because it is a manual 2nd implementation and sometimes it doesn't return the same result) and it doesn't need a dask activation class nor dask compatible alternatives.

## Bonus: computation graph!
(needs to be right clicked and downloaded or opened on a new tab)

In [14]:
rhat_einstats(ds, method="rank", dask="allowed").mu.data.visualize()

dot: graph is too large for cairo-renderer bitmaps. Scaling by 0.953749 to fit
